<font size=12, color=blue>  <center> <b>Máquinas Discriminativas Profundas

<font size=6, color=blue>  <center> <b> (*Deep Learning*)

<font size=6, color=green>  <center> <b>Ejemplo práctico en laboratorio

#### Práctica sobre aprendizaje profundo en la que se mostrarán algunos ejemplos de este tipo de técnicas, como los autocodificadores, la técnica de "drop-out" o las redes convolucionales (CNNs)

<font size=4, color=blue> Magic para representaciones on-line

In [ ]:
%matplotlib inline

<font size=4, color=blue> Se importan algunas librerías básicas

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import metodosDL as mdl

<font size=4, color=blue> A continuación se cargan los datos de la base de datos MNIST (números manuscritos)

In [ ]:
import gzip

def carga_MNIST_patrones(fichero):
        # Lectura de los datos MNIST con el formato de Yann LeCun
        with gzip.open(fichero, 'rb') as f:
            patrones = np.frombuffer(f.read(), np.uint8, offset=16)
        # Los patrones son vectores que contienen imágenes 2D en escala de grises
        # patrones = patrones.reshape(-1, 28, 28)
        # Se agrupan los patrones por filas (cada patrón es una fila, cada columna un pixel)
        patrones = patrones.reshape(-1,784)
        # Conversión de bytes a float32 en el rango [0,1].
        return patrones / np.float32(255)
    
def carga_MNIST_etiquetas(fichero):
        # Lectura de las etiquetas en el formato de Yann LeCun
        with gzip.open(fichero, 'rb') as f:
            etiquetas = np.frombuffer(f.read(), np.uint8, offset=8)
        # Las etiquetas son valores enteros
        return etiquetas

xTrain = carga_MNIST_patrones('train-images-idx3-ubyte.gz')
yTrain = carga_MNIST_etiquetas('train-labels-idx1-ubyte.gz')
xTest = carga_MNIST_patrones('t10k-images-idx3-ubyte.gz')
yTest = carga_MNIST_etiquetas('t10k-labels-idx1-ubyte.gz') 

# Los datos de entrenamiento se dividen en conjuntos de entrenamiento y de validación
xTrain, xVal = xTrain[:-10000], xTrain[-10000:]
yTrain, yVal = yTrain[:-10000], yTrain[-10000:]

print('Las imágenes se agrupan en una matriz, donde cada fila es una imagen con 784 píxeles (28x28)\r\n')
print('Tamaño de la matriz de patrones de entrenamiento: %d x %d'%(xTrain.shape))
print('Tamaño de la matriz de patrones de validación: %d x %d'%(xVal.shape))
print('Tamaño de la matriz de patrones de test: %d x %d'%(xTest.shape))
print(' ')
print('Tamaño de las etiquetas de los patrones de entrenamiento: %s'%(str(yTrain.shape)))
print('Tamaño de las etiquetas de los patrones de validación: %s'%(str(yVal.shape)))
print('Tamaño de las etiquetas de los patrones de test: %s'%(str(yTest.shape)))

<font size=4, color=blue> Se representa un dígito (ejemplo de los datos)

In [ ]:
indice=1
imagen = xTrain[indice,:]
imagen=imagen.reshape(28,28)
etiqueta=yTrain[indice]
fig, eje = plt.subplots(figsize=(5, 5))
eje.imshow(imagen, cmap='gray')
eje.set_title('{label}'.format(label=etiqueta))

<font size=4, color=blue> Se observa el rango de valores de los patrones

In [ ]:
# Se calculan los valores mínimo y máximo de los pixeles del patrón que se ha dibujado
valorMin=np.min(xTrain[indice,:])
valorMax=np.max(xTrain[indice,:])
print('Valor mínimo de los píxeles del patrón : %1.3f'%(valorMin))
print('Valor máximo de los píxeles del patrón : %1.3f'%(valorMax))

<font size=4, color=blue> Se representan ahora ejemplos de cada clase (el primero de cada clase en el conjunto de entrenamiento)

In [ ]:
indices=[]
# Se busca la posición en la que se encuentra el primer patrón de cada clase
for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

fig, ejes = plt.subplots(1, 10, figsize=(19, 2.5), subplot_kw={'xticks': [], 'yticks': []})
fig.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejes.flat, indices):
    imagen = xTrain[k,:]
    imagen=imagen.reshape(28,28)
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('{label}'.format(label=etiqueta))


<font size=4, color=blue> Por cuestiones de carga computacional se va a utilizar una menor resolución diezmando


In [ ]:
# Se diezman las imágenes de los conjuntos de entrenamiento, validación y test
# Se pueden utilizar resoluciones de:
#   28 x 28
#   14 x 14
#   10 x 10
#
resPixel=10

if resPixel==28:
    pixeles=np.linspace(0,27,num=28)  # para mantener 28 x 28
elif resPixel==14:
    pixeles=np.linspace(0,26,num=14)  # para diezmar a 14 x 14
elif resPixel==10:
    pixeles=np.linspace(0,27,num=10)  # para diezmar a 10 x 10

indDown=[]

for ka in pixeles:
    for kb in pixeles:
        indDown.append(int(ka)*28+int(kb))       

xTrainD=xTrain[:,indDown]
xValD=xVal[:,indDown]
xTestD=xTest[:,indDown]

fig, ejes = plt.subplots(1, 10, figsize=(19, 2.5), subplot_kw={'xticks': [], 'yticks': []})
fig.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejes.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('{label}'.format(label=etiqueta))

<font size=4, color=blue> Para reducir la carga computacional se realiza un muestreo, reduciendo el número de imágenes de entrenamiento por un factor "*factorS*"

In [ ]:
# Se muestrean los patrones del conjunto de entrenamiento
factorS=25    # Factor de muestreo (el número de muestras se divide por este factor)
#indTrainS=range(0,len(yTrain),factorS)
indTrainS=range(0,int(len(yTrain)/factorS))
xTrainDS=xTrainD[indTrainS,:]
yTrainDS=yTrain[indTrainS]

print('Tamaño de la matriz de patrones de entrenamiento: %d x %d'%(xTrainDS.shape))
print('Tamaño de la matriz de patrones de validación: %d x %d'%(xValD.shape))
print('Tamaño de la matriz de patrones de test: %d x %d'%(xTestD.shape))


<font size=4, color=blue>ONE-HOT ENCODING: Habitualmente, para una clasificación multiclase se utiliza una red con M salidas, una por cada clase. La referencia de la salida para el patrón de la clase *i*-ésima es un vector con M-1 ceros y un uno en la posición *i*-ésima. Se crea por tanto una matriz con los vectores de referencia para cada patrón


In [ ]:
eTrainDS=np.zeros((len(yTrainDS),10))
for k in range(len(yTrainDS)):
    aux=yTrainDS[k]
    eTrainDS[k,aux]=1
print('Tamaño de la matriz de etiquetas de referencia: %d x %d'%(eTrainDS.shape)) 

<font size=4, color=blue>Se muestra la referencia de la salida para un cierto patrón

In [ ]:
indice=0
print('Patrón de indice %d - Clase = %d'%(indice,yTrainDS[indice]))
print(eTrainDS[indice,:])
imagen = xTrainDS[indice,:]
imagen=imagen.reshape(resPixel,resPixel)
etiqueta=yTrainDS[indice]
fig, eje = plt.subplots(figsize=(5, 5))
eje.imshow(imagen, cmap='gray')
eje.set_title('{label}'.format(label=etiqueta))

<br>
<font size=6, color=green>Entrenamiento de una red neuronal no profunda 

<font size=4, color=blue>En primer lugar se definen los parámetros de la red, que es un perceptrón multicapa (MLP) de una única capa oculta

In [ ]:
fCoste='entropia'             # Tipo de función de coste ('mmse', 'entropia' ,'wmmse')
opt='gradiente'               # Tipo de optimizador ('gradiente', 'momento')
tAct=['tanh','softmax']       # Tipos de activación de las neuronas de la capa oculta y de la capa de salida
paso=[1e-3]                   # Parametro de paso de la actualización por gradiente
Nn=225                        # Número de neuronas de la capa oculta 
Niter=250                     # Número de iteraciones para la actualización por gradiente
Nbatch=0                      # Número de muestras del mini-batch (0 para modo Batch)
Nep=[Niter,Nbatch]            # Parámetros agrupados

(Np,Ne)=xTrainDS.shape
(Nada,Ns)=eTrainDS.shape

# Inicialización de los pesos de la capa oculta y de la capa de salida
inicializacionExterna=True
if inicializacionExterna:
    woini = 0.2*np.random.rand(Ne+1,Nn)-0.1
    wsini = 0.2*np.random.rand(Nn+1,Ns)-0.1
    W=[woini,wsini]
else:
    W=mdl.entrena_mlp(xTrainDS,eTrainDS,[Nn,[]],[0,0])[0]
    woini=W[0]
    wsini=W[1]
    

<font size=4, color=blue>Se realiza el entrenamiento del MLP y se representa la evolución del error cuadrático entre la salida de la red y los vectores de referencia para cada patrón

In [ ]:
(W, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,W,Nep,fCoste=fCoste,optimizador=opt,tAct=tAct)[0:3]

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del coste a minimizar', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Coste : %s' % (fCoste), fontdict=font)

<font size=4, color=blue>Se obtiene la salida de la red para los patrones de entrenamiento, los de validación y los de test y se estiman la probabilidad de acierto obtenidas sobre los 3 conjuntos de datos

In [ ]:
(oTrain,xOculta)=mdl.mlp(xTrainDS,W,tAct)
(oVal,xOculta)=mdl.mlp(xValD,W,tAct)
(oTest,xOculta)=mdl.mlp(xTestD,W,tAct)

yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

diferencia=yTrainE-yTrainDS
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

diferencia=yValE-yVal
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaVal=(100.0*len(indAcierto))/len(yVal)

diferencia=yTestE-yTest
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
indError = [i for (i, val) in enumerate(diferencia) if val != 0]
PaTest=(100.0*len(indAcierto))/len(yTest)

print('Probabilidad de acierto (Entrenamiento): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Validación): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<font size=4, color=blue>Se pueden ver un ejemplo de patrón clasificado erróneamente

In [ ]:
indiceError=0
indice=indError[indiceError];
imagen = xTestD[indice,:]
imagen=imagen.reshape(resPixel,resPixel)
etiqueta=yTest[indice]
fig, eje = plt.subplots(figsize=(5, 5))
#eje.title('{label}'.format(label=etiqueta))
eje.imshow(imagen, cmap='gray')
print("La etiqueta correcta es %s y la red predice %s"%(etiqueta,yTestE[indice]))

<font size=4, color=blue>Más ejemplos de patrones clasificados erróneamente

In [ ]:
indices=range(30)
resI=int(np.sqrt(Ne))

fig, ejes = plt.subplots(3, 10, figsize=(20, 8), subplot_kw={'xticks': [], 'yticks': []})
fig.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejes.flat, indices):
    imagen = xTestD[indError[k],:]
    imagen=imagen.reshape(resPixel,resPixel)
    eje.set_title('%d -> %d'%(yTest[indError[k]],yTestE[indError[k]]), fontsize=16)
    eje.imshow(imagen, cmap='gray')

<font size=4, color=blue> Se pueden representar los coeficientes de una neurona específica

In [ ]:
indice=0

imagen = W[0][0:Ne,indice]
resI=int(np.sqrt(Ne))
imagen=np.abs(imagen.reshape(resI,resI))
fig, eje = plt.subplots(figsize=(8, 8))
eje.set_title('Pesos de la neurona {label}'.format(label=indice+1))
eje.imshow(imagen, cmap='gray')

<font size=4, color=blue> Se representan los pesos obtenidos en algunas de las neuronas

In [ ]:
indices=range(100)
resI=int(np.sqrt(Ne))

fig, ejes = plt.subplots(5, 20, figsize=(20, 6), subplot_kw={'xticks': [], 'yticks': []})
fig.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejes.flat, indices):
    imagen = W[0][0:Ne,k]
    imagen=np.abs(imagen.reshape(resI,resI))
    eje.imshow(imagen, cmap='gray')

<font size=4, color=blue> Se representa la evolución de la tasa de acierto con las iteraciones

In [ ]:
W=[woini,wsini]
NiterPaso=50
NrepBucle=60
evoPa=np.zeros((3,NrepBucle))

for kbucle in range(NrepBucle):
    (W, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,W,[NiterPaso,Nbatch],
                                       fCoste=fCoste,optimizador=opt,tAct=tAct)[0:3]
    (oTrain,xOculta)=mdl.mlp(xTrainDS,W,tAct)
    (oVal,xOculta)=mdl.mlp(xValD,W,tAct)
    (oTest,xOculta)=mdl.mlp(xTestD,W,tAct)

    yTrainE=oTrain.argmax(axis=1)
    yValE=oVal.argmax(axis=1)
    yTestE=oTest.argmax(axis=1)

    diferencia=yTrainE-yTrainDS
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

    diferencia=yValE-yVal
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    PaVal=(100.0*len(indAcierto))/len(yVal)

    diferencia=yTestE-yTest
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
    PaTest=(100.0*len(indAcierto))/len(yTest)
    evoPa[:,kbucle]=[PaTrain,PaVal,PaTest]
    
font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
ejeIter=NiterPaso*(1+np.arange(NrepBucle))
plt.plot(ejeIter,evoPa[0,:],ejeIter,evoPa[1,:],ejeIter,evoPa[2,:])
plt.title('Evolucion de la Prob. Acierto', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Prob. Acierto (%)', fontdict=font)

print('Entrenamiento (azul) - Validación (Naranja) - Test (verde)')
print(' ')
print('Max. Pa (Entrenamiento): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[0,:]),NiterPaso*np.argmax(evoPa[0,:])))
print('Max. Pa (Validación): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[1,:]),NiterPaso*np.argmax(evoPa[1,:])))
print('Max. Pa (Test) : %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[2,:]),NiterPaso*np.argmax(evoPa[2,:])))
print('Resultado con validación (Test): %3.2f %%'%(evoPa[2,np.argmax(evoPa[1,:])]))

<br>
<font size=6, color=green> Entrenamiento de una red profunda
    
<font size=4, color=blue> Se entrena en este caso un MLP de 4 capas ocultas y una capa de salida

In [ ]:
fCoste='entropia' # Tipo de función de coste ('mmse', 'entropia' ,'wmmse')
opt='gradiente'   # Tipo de optimizador ('gradiente', 'momento')
                  # Tipos de activación de las neuronas de las capas oculta y de la capa de salida
tAct=['tanh','tanh','tanh','tanh','softmax']  

paso=[1e-3]       # Parametro de paso de la actualización por gradiente
Nneu1=225         # Número de neuronas de la primera capa oculta
Nneu2=225         # Número de neuronas de la segunda capa oculta
Nneu3=225         # Número de neuronas de la tercera capa oculta 
Nneu4=225         # Número de neuronas de la cuarta capa oculta 
Niter=250         # Número de iteraciones para la actualización por gradiente
Nbatch=250        # Número de muestras del mini-batch
Nep=[Niter,Nbatch]

(Np,Ne)=xTrainDS.shape
(Nada,Ns)=eTrainDS.shape

# Inicialización de los pesos de la capa oculta y de la capa de salida
inicializacionExterna=True
if inicializacionExterna:
    wo1ini = 0.2*np.random.rand(Ne+1,Nneu1)-0.1
    wo2ini = 0.2*np.random.rand(Nneu1+1,Nneu2)-0.1
    wo3ini = 0.2*np.random.rand(Nneu2+1,Nneu3)-0.1
    wo4ini = 0.2*np.random.rand(Nneu3+1,Nneu4)-0.1
    wsini = 0.2*np.random.rand(Nneu4+1,Ns)-0.1
    W=[wo1ini,wo2ini,wo3ini,wo4ini,wsini]
else:
    W=mdl.entrena_mlp(xTrainDS,eTrainDS,[Nneu1,Nneu2,Nneu3,Nneu4,[]],[0,0])[0]
    wo1ini=W[0]
    wo2ini=W[1]
    wo3ini=W[2]
    wo4ini=W[3]
    wsini=W[4]
    

In [ ]:
(W, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,W,Nep,fCoste=fCoste,optimizador=opt,tAct=tAct,paso=paso)[0:3]

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del coste a minimizar', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Coste : %s' % (fCoste), fontdict=font)

In [ ]:
# Se evalúan las prestaciones
oTrain=mdl.mlp(xTrainDS,W,tAct)[0]
oVal=mdl.mlp(xValD,W,tAct)[0]
oTest=mdl.mlp(xTestD,W,tAct)[0]

yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

diferencia=yTrainE-yTrainDS
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

diferencia=yValE-yVal
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaVal=(100.0*len(indAcierto))/len(yVal)

diferencia=yTestE-yTest
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
PaTest=(100.0*len(indAcierto))/len(yTest)

print('Probabilidad de acierto (Entrenamiento): %3.2f %%'%(PaTrain))
print('Probabilidad de acierto (Validación): %3.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %3.2f %%'%(PaTest))

<font size=4, color=blue> Se representa la evolución de la tasa de acierto con las iteraciones

In [ ]:
W=[wo1ini,wo2ini,wo3ini,wo4ini,wsini]
NiterPaso=50
NrepBucle=60
evoPa=np.zeros((3,NrepBucle))
for kbucle in range(NrepBucle):
    (W, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,W,[NiterPaso,Nbatch],fCoste=fCoste,optimizador=opt,tAct=tAct)[0:3]
    (oTrain,xOculta)=mdl.mlp(xTrainDS,W,tAct)
    (oVal,xOculta)=mdl.mlp(xValD,W,tAct)
    (oTest,xOculta)=mdl.mlp(xTestD,W,tAct)

    yTrainE=oTrain.argmax(axis=1)
    yValE=oVal.argmax(axis=1)
    yTestE=oTest.argmax(axis=1)

    diferencia=yTrainE-yTrainDS
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

    diferencia=yValE-yVal
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    PaVal=(100.0*len(indAcierto))/len(yVal)

    diferencia=yTestE-yTest
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
    PaTest=(100.0*len(indAcierto))/len(yTest)
    evoPa[:,kbucle]=[PaTrain,PaVal,PaTest]
    
font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
ejeIter=NiterPaso*np.linspace(1,NrepBucle,NrepBucle)
plt.plot(ejeIter,evoPa[0,:],ejeIter,evoPa[1,:],ejeIter,evoPa[2,:])
plt.title('Evolucion de la Prob. Acierto', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Prob Acierto (%)', fontdict=font)

print('Entrenamiento (azul) - Validación (Naranja) - Test (verde)')
print(' ')
print('Max. Pa (Entrenamiento): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[0,:]),NiterPaso*np.argmax(evoPa[0,:])))
print('Max. Pa (Validación): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[1,:]),NiterPaso*np.argmax(evoPa[1,:])))
print('Max. Pa (Test) : %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[2,:]),NiterPaso*np.argmax(evoPa[2,:])))
print('Resultado con validación (Test): %3.2f %%'%(evoPa[2,np.argmax(evoPa[1,:])]))

<br>
<font size=6, color=green>Entrenamiento de un autocodificador sin ruido

<font size=4, color=blue>Se entrenará ahora un autocodificador para una red MLP

In [ ]:
# Se inicializan los parámetros del codificador y de su entrenamiento
tAct=['tanh','sigmoid']         # Tipos de activación de las neuronas de la capa oculta y de la capa de salida
paso=[1e-3]                     # Parámetro de paso de la actualización por gradiente
Nneu=225                        # Número de neuronas de la capa oculta 
Niter=250                       # Número de iteraciones para la actualización por gradiente

(Np,Ne)=xTrainDS.shape
(Nada,Ns)=eTrainDS.shape
# Inicialización de los pesos de la capa oculta y de la capa de salida
weini = 0.2*np.random.rand(Ne+1,Nneu)-0.1
wrini = 0.2*np.random.rand(Nneu+1,Ne)-0.1

we1=weini
wr1=wrini

In [ ]:
(we1, wr1, coste, paso)=mdl.entrena_AE(xTrainDS,we1,wr1,Niter,tAct,paso)

# En realidad, un autocodificador sin ruido se puede ver como una red neuronal en la que la salida de referencia es
# igual a los patrones de entrada
#
# W=[we1,wr1]
# (W, paso, coste)=mdl.entrena_mlp(xTrainDS,xTrainDS,W,[Niter,0],tAct=tAct,paso=paso)[0:3]
# we1=W[0]
# wr1=W[1]

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del MSE para codificador sin ruido', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('MSE', fontdict=font)

<font size=4, color=blue>Se representan las reconstrucciones obtenidas a partir del codificador

In [ ]:
(xTrainDrec,xTrainE1)=mdl.mlp(xTrainD,[we1,wr1],tAct)

indices=[]

for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

figA, ejesA = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figA.subplots_adjust(hspace=0.3, wspace=0.05)
figB, ejesB = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figB.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejesA.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('{label}'.format(label=etiqueta))
for eje, k in zip(ejesB.flat, indices):    
    imagen = xTrainDrec[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray')

<font size=4, color=blue>Se representan los pesos de algunas neuronas de la capa oculta (codificador)

In [ ]:
indice=0
imagen = we1[0:Ne,indice]
resI=int(np.sqrt(Ne))
imagen=np.abs(imagen.reshape(resI,resI))
fig, eje = plt.subplots(figsize=(6, 6))
eje.set_title('Pesos de la neurona {label} (AE)'.format(label=indice+1))
eje.imshow(imagen, cmap='gray')

In [ ]:
indices=range(100)
resI=int(np.sqrt(Ne))

fig, ejes = plt.subplots(5, 20, figsize=(20, 6), subplot_kw={'xticks': [], 'yticks': []})
fig.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejes.flat, indices):
    imagen = we1[0:Ne,k]
    imagen=np.abs(imagen.reshape(resI,resI))
    eje.imshow(imagen, cmap='gray')

<font size=4, color=blue>Se representan las proyecciones de algunos patrones

In [ ]:
indices=[]

for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

figA, ejesA = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figA.subplots_adjust(hspace=0.3, wspace=0.05)
figB, ejesB = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figB.subplots_adjust(hspace=0.3, wspace=0.05)
figC, ejesC = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figC.subplots_adjust(hspace=0.3, wspace=0.05)



for eje, k in zip(ejesA.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('{label}'.format(label=etiqueta))
for eje, k in zip(ejesB.flat, indices):    
    imagen = xTrainE1[0][k,:]
    imagen=imagen.reshape(int(np.sqrt(Nneu)),int(np.sqrt(Nneu)))
    eje.imshow(imagen, cmap='gray')
for eje, k in zip(ejesC.flat, indices):    
    imagen = xTrainDrec[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray')    

<br>
<font size=6, color=green>Entrenamiento de un autocodificador con ruido
    
<font size=4, color=blue> Ahora se entrena un autocodificador con ruido en la entrada

In [ ]:
# Se inicializan los parámetros del codificador y de su entrenamiento
tAct=['tanh','sigmoid']       # Tipos de activación de las neuronas de la capa oculta y de la capa de salida
paso=[1e-3]                   # Parametro de paso de la actualización por gradiente
Nneu=225                      # Número de neuronas de la capa oculta 
Niter=250                     # Número de iteraciones para la actualización por gradiente
pRuido=0.25                   # Probabilidad de poner a cero una cierta entrada

# Inicialización de los pesos de la capa oculta y de la capa de salida
# weini = 0.2*np.random.rand(Ne+1,Nneu)-0.1
# wdini = 0.2*np.random.rand(Nneu+1,Ne)-0.1

we1n=weini
wr1n=wrini

In [ ]:
(we1n, wr1n, coste, paso)=mdl.entrena_DAE(xTrainDS,we1n,wr1n,Niter,tAct,paso,pRuido)

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del MSE para un codificador con ruido', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('MSE', fontdict=font)

<font size=4, color=blue>Se representan las reconstrucciones obtenidas a partir del codificador

In [ ]:
(xTrainDrec,xTrainE1n)=mdl.mlp(xTrainD,[we1n,wr1n],tAct)

indices=[]

for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

figA, ejesA = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figA.subplots_adjust(hspace=0.3, wspace=0.05)
figB, ejesB = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figB.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejesA.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('a')
    eje.set_title('{label}'.format(label=etiqueta))
for eje, k in zip(ejesB.flat, indices):    
    imagen = xTrainDrec[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray')

<font size=4, color=blue>Se representan los pesos de algunas neuronas de la capa oculta (codificador)

In [ ]:
indice=0

imagen = we1[0:Ne,indice]
imagenN = we1n[0:Ne,indice]
resI=int(np.sqrt(Ne))
imagen=np.abs(imagen.reshape(resI,resI))
imagenN=np.abs(imagenN.reshape(resI,resI))

fig, eje = plt.subplots(nrows=1, ncols=2, sharex=True, figsize=(13, 6))
fig.subplots_adjust(hspace=0.3)
eje[0].set_title('Pesos de la neurona {label} (AE)'.format(label=indice+1))
eje[0].imshow(imagen, cmap='gray')
eje[1].set_title('Pesos de la neurona {label} (DAE)'.format(label=indice+1))
eje[1].imshow(imagenN, cmap='gray')


In [ ]:
indices=range(100)
resI=int(np.sqrt(Ne))

fig, ejes = plt.subplots(5, 20, figsize=(19, 5), subplot_kw={'xticks': [], 'yticks': []})
fig.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejes.flat, indices):
    imagen = we1n[0:Ne,k]
    imagen=np.abs(imagen.reshape(resI,resI))
    eje.imshow(imagen, cmap='gray')

<font size=4, color=blue>Se representan las proyecciones de algunos patrones

In [ ]:
indices=[]

for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

figA, ejesA = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figA.subplots_adjust(hspace=0.3, wspace=0.05)
figB, ejesB = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figB.subplots_adjust(hspace=0.3, wspace=0.05)
figC, ejesC = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figC.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejesA.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('{label}'.format(label=etiqueta))
for eje, k in zip(ejesB.flat, indices):    
    imagen = xTrainE1n[0][k,:]
    imagen=imagen.reshape(int(np.sqrt(Nneu)),int(np.sqrt(Nneu)))
    eje.imshow(imagen, cmap='gray')
for eje, k in zip(ejesC.flat, indices):    
    imagen = xTrainDrec[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray')    


In [ ]:
digito=0

imagenAE = xTrainE1[0][indices[digito],:]
imagenAE=imagenAE.reshape(int(np.sqrt(Nneu)),int(np.sqrt(Nneu)))

imagenDAE = xTrainE1n[0][indices[digito],:]
imagenDAE=imagenDAE.reshape(int(np.sqrt(Nneu)),int(np.sqrt(Nneu)))

fig, eje = plt.subplots(nrows=1, ncols=2, sharex=True, figsize=(13, 6))
fig.subplots_adjust(hspace=0.3)
eje[0].set_title('Proyección dígito {label} (AE)'.format(label=digito))
eje[0].imshow(imagenAE, cmap='gray')
eje[1].set_title('Proyección dígito {label} (DAE)'.format(label=digito))
eje[1].imshow(imagenDAE, cmap='gray')

<br>
<font size=6, color=green>Autocodificadores "apilados"
<br>    
<font size=4, color=blue>Se utilizarán ahora autoencoders para obtener los parámetros de las capas ocultas de una red profunda. A esta alternativa se le denomina autocodificadores apilados, o en inglés (Stacked Denoising Autoencoders)

In [ ]:
# Se comienza por definir los parámetros básicos del sistema
tActAE1=['tanh','sigmoid']  # Tipos de activación de las neuronas de la capas oculta y de la capa de salida del AE-1
tActAE2=['tanh','tanh']     # Tipos de activación de las neuronas de la capas oculta y de la capa de salida del AE-2
tActAE3=['tanh','tanh']     # Tipos de activación de las neuronas de la capas oculta y de la capa de salida del AE-3
paso=[1e-3]       # Parametro de paso de la actualización por gradiente
Nneu1=225         # Número de neuronas de la primera capa oculta
Nneu2=225         # Número de neuronas de la segunda capa oculta
Nneu3=225         # Número de neuronas de la tercera capa oculta 
Niter=1000        # Número de iteraciones para la actualización por gradiente
pRuido=0.25       # Probabilidad de anular una de las entradas

(Np,Ne)=xTrainDS.shape
# Inicialización de los pesos de los autocodificadores
we1ini = 0.2*np.random.rand(Ne+1,Nneu1)-0.1
we2ini = 0.2*np.random.rand(Nneu1+1,Nneu2)-0.1
we3ini = 0.2*np.random.rand(Nneu2+1,Nneu3)-0.1
# Inicialización de los pesos de reconstrucción
wr1ini = 0.2*np.random.rand(Nneu1+1,Ne)-0.1
wr2ini = 0.2*np.random.rand(Nneu2+1,Nneu1)-0.1
wr3ini = 0.2*np.random.rand(Nneu3+1,Nneu2)-0.1
# Inicialización de los pesos
we1=we1ini
we2=we2ini
we3=we3ini
wr1=wr1ini
wr2=wr2ini
wr3=wr3ini

<font size=4, color=blue> Se entrena el primer AE

In [ ]:
(we1, wr1, coste, paso)=mdl.entrena_DAE(xTrainDS,we1,wr1,Niter,tActAE1,paso,pRuido)

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del MSE para el primer AE', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('MSE', fontdict=font)

<font size=4, color=blue>Se realiza la proyección obtenida con el primer autocodificador

In [ ]:
xTrainDSE1=mdl.mlp(xTrainDS,[we1,wr1],tActAE1)[1][0]
xTrainDE1=mdl.mlp(xTrainD,[we1,wr1],tActAE1)[1][0]
xTestDE1=mdl.mlp(xTestD,[we1,wr1],tActAE1)[1][0]
xValDE1=mdl.mlp(xValD,[we1,wr1],tActAE1)[1][0]

<font size=4, color=blue> Se entrena el segundo AE

In [ ]:
(we2, wr2, coste, paso)=mdl.entrena_DAE(xTrainDSE1,we2,wr2,Niter,tActAE2,paso,pRuido)

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del MSE para el segundo AE', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('MSE', fontdict=font)

<font size=4, color=blue>Se realiza la proyección obtenida con el segundo autocodificador

In [ ]:
xTrainDSE2=mdl.mlp(xTrainDSE1,[we2,wr2],tActAE2)[1][0]
xTrainDE2=mdl.mlp(xTrainDE1,[we2,wr2],tActAE2)[1][0]
xTestDE2=mdl.mlp(xTestDE1,[we2,wr2],tActAE2)[1][0]
xValDE2=mdl.mlp(xValDE1,[we2,wr2],tActAE2)[1][0]

<font size=4, color=blue>Se entrena el tercer AE

In [ ]:
(we3, wr3, coste, paso)=mdl.entrena_DAE(xTrainDSE2,we3,wr3,Niter,tActAE3,paso,pRuido)

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del MSE para el tercer AE', fontdict=font)
plt.xlabel('Iteracion', fontdict=font)
plt.ylabel('MSE', fontdict=font)

<font size=4, color=blue> Se realiza la proyección obtenida con el tercer autocodificador

In [ ]:
xTrainDSE3=mdl.mlp(xTrainDSE2,[we3,wr3],tActAE3)[1][0]
xTrainDE3=mdl.mlp(xTrainDE2,[we3,wr3],tActAE3)[1][0]
xTestDE3=mdl.mlp(xTestDE2,[we3,wr3],tActAE3)[1][0]
xValDE3=mdl.mlp(xValDE2,[we3,wr3],tActAE3)[1][0]

<font size=4, color=blue> Se visualizan las proyecciones de los 3 autocodificadores

In [ ]:
indices=[]

for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

figA, ejesA = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figA.subplots_adjust(hspace=0.3, wspace=0.05)
figB, ejesB = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figB.subplots_adjust(hspace=0.3, wspace=0.05)
figC, ejesC = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figC.subplots_adjust(hspace=0.3, wspace=0.05)
figD, ejesD = plt.subplots(1, 10, figsize=(20, 4), subplot_kw={'xticks': [], 'yticks': []})
figD.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejesA.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('{label}'.format(label=etiqueta))
for eje, k in zip(ejesB.flat, indices):    
    imagen = xTrainDE1[k,:]
    imagen=imagen.reshape(int(np.sqrt(Nneu1)),int(np.sqrt(Nneu1)))
    eje.imshow(imagen, cmap='gray')
for eje, k in zip(ejesC.flat, indices):    
    imagen = xTrainDE2[k,:]
    imagen=imagen.reshape(int(np.sqrt(Nneu2)),int(np.sqrt(Nneu2)))
    eje.imshow(imagen, cmap='gray')
for eje, k in zip(ejesD.flat, indices):    
    imagen = xTrainDE3[k,:]
    imagen=imagen.reshape(int(np.sqrt(Nneu3)),int(np.sqrt(Nneu3)))
    eje.imshow(imagen, cmap='gray')




<font size=4, color=blue> Se entrena ahora la etapa de salida (una capa oculta y una de salida)

In [ ]:
fCoste='entropia'                # Tipo de función de coste ('mmse', 'entropia' ,'wmmse')
opt='gradiente'                  # Tipo de optimizador ('gradiente', 'momento')
tActFin=['tanh','softmax']       # Tipos de activación de las neuronas de la capa oculta y de la capa de salida
paso=1e-3                        # Parametro de paso de la actualización por gradiente
NneuFin=150                      # Número de neuronas de la capa oculta 
Niter=1000                       # Número de iteraciones para la actualización por gradiente
Nbatch=250                       # Número de patrones del mini-batch 
Nep=[Niter,Nbatch]
                                 
(Np,Ne)=xTrainDSE3.shape
(Nada,Ns)=eTrainDS.shape

# Inicialización de los pesos de la capa oculta y de la capa de salida
inicializacionExterna=True
if inicializacionExterna:
    woini = 0.2*np.random.rand(Ne+1,NneuFin)-0.1
    wsini = 0.2*np.random.rand(NneuFin+1,Ns)-0.1
    Wfin=[woini,wsini]
else:
    Wfin=mdl.entrena_mlp(xTrainDSE3,eTrainDS,[NneuFin,[]],[0,0])[0]
    woini=Wfin[0]
    wsini=Wfin[1]


In [ ]:
#Niter=3000
#Nep=[Niter,250]
(Wfin, paso, coste) = mdl.entrena_mlp(xTrainDSE3,eTrainDS,Wfin,Nep,fCoste=fCoste,optimizador=opt,tAct=tActFin)[0:3]

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del coste a minimizar', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Coste : %s' % (fCoste), fontdict=font)

<font size=4, color=blue> Se estiman las prestaciones obtenidas con esta etapa

In [ ]:
oTrain=mdl.mlp(xTrainDSE3,Wfin,tActFin)[0]
oVal=mdl.mlp(xValDE3,Wfin,tActFin)[0]
oTest=mdl.mlp(xTestDE3,Wfin,tActFin)[0]

yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

diferencia=yTrainE-yTrainDS
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

diferencia=yValE-yVal
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaVal=(100.0*len(indAcierto))/len(yVal)

diferencia=yTestE-yTest
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
PaTest=(100.0*len(indAcierto))/len(yTest)

print('Probabilidad de acierto (Entrenamiento): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Validación): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<font size=4, color=blue> Imágenes reconstruidas a partir de las representaciones obtenidas por los distintos autocodificadores

In [ ]:
# Se proyectan las salidas de los autocodificadores
xTrainDE1=mdl.mlp(xTrainD,[we1,wr1],tActAE1)[1][0]
xTrainDE2=mdl.mlp(xTrainDE1,[we2,wr2],tActAE2)[1][0]
xTrainDE3=mdl.mlp(xTrainDE2,[we3,wr3],tActAE3)[1][0]

# Se reconstruyen dichas proyecciones
xTrainDrec1=mdl.mlp(xTrainDE1,[wr1],[tActAE1[1]])[0]
xTrainDrec2=mdl.mlp(xTrainDE2,[wr2,wr1],[tActAE2[1],tActAE1[1]])[0]
xTrainDrec3=mdl.mlp(xTrainDE3,[wr3,wr2,wr1],[tActAE3[1],tActAE2[1],tActAE1[1]])[0]

indices=[]

for k in range(10):
    indNum = [i for (i, val) in enumerate(yTrain[0:30]) if val == int(k)]
    indices.append(indNum[0])

figA, ejesA = plt.subplots(1, 10, figsize=(12, 3), subplot_kw={'xticks': [], 'yticks': []})
figA.subplots_adjust(hspace=0.3, wspace=0.05)
figB, ejesB = plt.subplots(1, 10, figsize=(12, 3), subplot_kw={'xticks': [], 'yticks': []})
figB.subplots_adjust(hspace=0.3, wspace=0.05)
figC, ejesC = plt.subplots(1, 10, figsize=(12, 3), subplot_kw={'xticks': [], 'yticks': []})
figC.subplots_adjust(hspace=0.3, wspace=0.05)
figD, ejesD = plt.subplots(1, 10, figsize=(12, 3), subplot_kw={'xticks': [], 'yticks': []})
figD.subplots_adjust(hspace=0.3, wspace=0.05)

for eje, k in zip(ejesA.flat, indices):
    imagen = xTrainD[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    etiqueta = yTrain[k]
    eje.imshow(imagen, cmap='gray')
    eje.set_title('a')
    eje.set_title('{label}'.format(label=etiqueta))
    
for eje, k in zip(ejesB.flat, indices):    
    imagen = xTrainDrec1[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray') 
    
for eje, k in zip(ejesC.flat, indices):    
    imagen = xTrainDrec2[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray')
    
for eje, k in zip(ejesD.flat, indices):    
    imagen = xTrainDrec3[k,:]
    imagen=imagen.reshape(len(pixeles),len(pixeles))
    eje.imshow(imagen, cmap='gray')


<font size=4, color=blue>Se realiza el ajuste fino sobre la red global

In [ ]:
# Se agrupan en una lista los pesos de cada capa y las funciones de activación de cada capa
Wtotal=[we1,we2,we3,Wfin[0],Wfin[1]] 
paso=[1e-3]
tActTotal=[tActAE1[0], tActAE2[0], tActAE3[0], tActFin[0], tActFin[1]]
Niter=50                # Número de iteraciones para la actualización por gradiente
Nbatch=250              # Número de patrones del mini-batch 
Nep=[Niter,Nbatch]

In [ ]:
# Se entrena la red global con las 4 capas ocultas y 1 capa de salida
Niter=1000
Nep=[Niter,Nbatch]
(Wtotal, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,Wtotal,Nep,fCoste=fCoste,
                                        optimizador=opt,tAct=tActTotal,paso=paso)[0:3]

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del coste a minimizar', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Coste : %s' % (fCoste), fontdict=font)

<font size=4, color=blue> Se estiman las prestaciones obtenidas con la red completa

In [ ]:
oTrain=mdl.mlp(xTrainDS,Wtotal,tActTotal)[0]
oVal=mdl.mlp(xValD,Wtotal,tActTotal)[0]
oTest=mdl.mlp(xTestD,Wtotal,tActTotal)[0]

yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

diferencia=yTrainE-yTrainDS
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

diferencia=yValE-yVal
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaVal=(100.0*len(indAcierto))/len(yVal)

diferencia=yTestE-yTest
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
PaTest=(100.0*len(indAcierto))/len(yTest)

print('Probabilidad de acierto (Entrenamiento): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Validación): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<br>
<font size=6, color=green>Red neuronal profunda con Drop-Out
    
<font size=4, color=blue>Se entrenará ahora una red neuronal de varias capas ocultas con inicialización aleatoria, Drop-Out, y funciones de activación ReLU (Rectified Linear Units)

In [ ]:
# Se comienza por definir los parámetros básicos del sistema
fCoste='entropia'        # Tipo de función de coste ('mmse', 'entropia' ,'wmmse')
opt='gradiente'          # Tipo de optimizador ('gradiente', 'momento')
# Tipos de activación de las neuronas de las capas oculta y de la capa de salida
tAct=['relu','relu','relu','relu','softmax']
                         
paso=[1e-3]              # Parametro de paso de la actualización por gradiente
Nneu1=225                # Número de neuronas de la primera capa oculta
Nneu2=225                # Número de neuronas de la segunda capa oculta
Nneu3=225                # Número de neuronas de la tercera capa oculta 
Nneu4=225                # Número de neuronas de la tercera capa oculta 
Niter=500                # Número de iteraciones para la actualización por gradiente
Nbatch=250               # Número de muestras del mini-batch 
Nep=[Niter,Nbatch]
pDO=[0.1,0.25,0.25,0.25,0.25]  # Probabilidades de Drop-Out (de la entrada y de las capas ocultas)

# Se inicializan los pesos
Wini = mdl.entrena_mlp(xTrainDS,eTrainDS,[Nneu1,Nneu2,Nneu3,Nneu4,[]],[0,0])[0]
W=list(Wini)

In [ ]:
#Niter=2000
#Nep=[Niter,250]
(W, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,W,Nep,fCoste=fCoste,
                                   optimizador=opt,tAct=tAct,paso=paso,pDO=pDO)[0:3]

font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
plt.plot(range(Niter+1),coste)
plt.title('Evolucion del coste a minimizar', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Coste : %s' % (fCoste), fontdict=font)

<font size=4, color=blue> Se estiman las prestaciones obtenidas con esta red (con Drop-Out)

In [ ]:
oTrain=mdl.mlp(xTrainDS,W,tAct)[0]
oVal=mdl.mlp(xValD,W,tAct)[0]
oTest=mdl.mlp(xTestD,W,tAct)[0]

yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

diferencia=yTrainE-yTrainDS
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

diferencia=yValE-yVal
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaVal=(100.0*len(indAcierto))/len(yVal)

diferencia=yTestE-yTest
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
PaTest=(100.0*len(indAcierto))/len(yTest)

print('Probabilidad de acierto (Entrenamiento): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Validación): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<font size=4, color=blue> Se representa la evolución de la tasa de acierto con las iteraciones

In [ ]:
W=list(Wini)
pEnt=0.1
pOcu=0.25
pDO=[pEnt,pOcu,pOcu,pOcu,pOcu]
NiterPaso=50
NrepBucle=60
evoPa=np.zeros((3,NrepBucle))
for kbucle in range(NrepBucle):
    (W, paso, coste) = mdl.entrena_mlp(xTrainDS,eTrainDS,W,[NiterPaso,Nbatch],fCoste=fCoste,
                                   optimizador=opt,tAct=tAct,paso=paso,pDO=pDO)[0:3]
    (oTrain,xOculta)=mdl.mlp(xTrainDS,W,tAct)
    (oVal,xOculta)=mdl.mlp(xValD,W,tAct)
    (oTest,xOculta)=mdl.mlp(xTestD,W,tAct)

    yTrainE=oTrain.argmax(axis=1)
    yValE=oVal.argmax(axis=1)
    yTestE=oTest.argmax(axis=1)

    diferencia=yTrainE-yTrainDS
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

    diferencia=yValE-yVal
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    PaVal=(100.0*len(indAcierto))/len(yVal)

    diferencia=yTestE-yTest
    indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
    indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
    PaTest=(100.0*len(indAcierto))/len(yTest)
    evoPa[:,kbucle]=[PaTrain,PaVal,PaTest]
    
font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
ejeIter=NiterPaso*np.linspace(1,NrepBucle,NrepBucle)
plt.plot(ejeIter,evoPa[0,:],ejeIter,evoPa[1,:],ejeIter,evoPa[2,:])
plt.title('Evolución de la Prob. Acierto', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Prob Acierto (%)', fontdict=font)

print('Entrenamiento (azul) - Validación (Naranja) - Test (verde)')
print(' ')
print('Max. Pa (Entrenamiento): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[0,:]),NiterPaso*np.argmax(evoPa[0,:])))
print('Max. Pa (Validación): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[1,:]),NiterPaso*np.argmax(evoPa[1,:])))
print('Max. Pa (Test) : %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[2,:]),NiterPaso*np.argmax(evoPa[2,:])))
print('Resultado con validación (Test): %3.2f %%'%(evoPa[2,np.argmax(evoPa[1,:])]))

<br>
<font size=6, color=green>Implementaciones con librerías de Python
    
<font size=5, color=red>Librería scikit-learn

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix

from sklearn.metrics import balanced_accuracy_score                 
from sklearn.metrics import precision_score 
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score 

from sklearn import preprocessing
from sklearn.neural_network import MLPClassifier

<font size=4, color=blue>Utilidades para normalización de los datos

In [ ]:
#- Normalización ------------------------------
flagNormaliza=False

if flagNormaliza:
    scaler = preprocessing.StandardScaler().fit(xTrainDS)
    #scaler = preprocessing.MinMaxScaler().fit(xTrainDS)
    #scaler = preprocessing.MaxAbsScaler().fit(xTrainDS)
    xTrainDS=scaler.transform(xTrainDS)
    xValD=scaler.transform(xValD)
    xTestD=scaler.transform(xTestD)

<font size=4, color=blue>Red neuronal de una única capa oculta

In [ ]:
Nneu=225
Niter=500

# Se define el modelo neuronal (arquitectura, y entrenamiento)
model = MLPClassifier(hidden_layer_sizes=(Nneu, ), activation='tanh', 
                      solver='adam', 
                      alpha=0.01,
                      max_iter=Niter)

# Se entrena la red MLP
model.fit(xTrainDS, yTrainDS)

In [ ]:
# Se evalúan las prestaciones
yTrainE = model.predict(xTrainDS)
yValE = model.predict(xValD)
yTestE = model.predict(xTestD)

diferencia=yTrainE-yTrainDS
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaTrain=(100.0*len(indAcierto))/len(yTrainDS)

diferencia=yValE-yVal
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
PaVal=(100.0*len(indAcierto))/len(yVal)

diferencia=yTestE-yTest
indAcierto = [i for (i, val) in enumerate(diferencia) if val == 0]
indFallo = [i for (i, val) in enumerate(diferencia) if val != 0]
PaTest=(100.0*len(indAcierto))/len(yTest)

print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

In [ ]:
# Se obtiene la matriz de confusión entre las 10 clases (matriz 10 x 10)
ConfMatrix=confusion_matrix(yTest,yTestE)
print('Matriz de confusión\n')
print(ConfMatrix)
print(' ')
# Se obtiene la tasa de acierto sobre el conjunto de Test
Accuracy=accuracy_score(yTest,yTestE)
print('Tasa de acierto sobre el conjunto de Test = %2.2f %%'%(100*Accuracy))

<font size=4, color=blue>Red neuronal de 4 capas ocultas

In [ ]:
Nneu1=225
Nneu2=225
Nneu3=225
Nneu4=225
Niter=500 

# Se define el modelo neuronal (arquitectura, y entrenamiento)
model = MLPClassifier(hidden_layer_sizes=(Nneu1,Nneu2,Nneu3,Nneu4, ), activation='tanh', 
                      solver='adam', 
                      alpha=0.01,
                      max_iter=Niter)

# Se entrena la red MLP
model.fit(xTrainDS, yTrainDS)

In [ ]:
# Se evalúan las prestaciones
yTrainE = model.predict(xTrainDS)
yValE = model.predict(xValD)
yTestE = model.predict(xTestD)

PaTrain=100*accuracy_score(yTrainDS,yTrainE)
PaVal=100*accuracy_score(yVal,yValE)
PaTest=100*accuracy_score(yTest,yTestE)

print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))


<font size=5, color=red>Librería Keras (TensorFlow)

<font size=4, color=blue>Red neuronal de una única capa oculta    

In [ ]:
import tensorflow as tf
#
# OS X - necesario para corregir un bug en la distribución actual de anaconda para OS X
import os
os.environ['KMP_DUPLICATE_LIB_OK']='True'
#

tf.keras.backend.clear_session()

Nneu=225
Niter=500
Nbatch=250

(Np,Ne)=xTrainDS.shape
(Nada,Ns)=eTrainDS.shape

flagDefineKerasAdd=True
    
if flagDefineKerasAdd:

    model = tf.keras.Sequential()
    model.add(tf.keras.Input(shape=(Ne,)))
    model.add(tf.keras.layers.Dense(Nneu, activation='tanh'))
    model.add(tf.keras.layers.Dense(Ns, activation='softmax'))
    
else:
    model = tf.keras.Sequential(
      [
          tf.keras.layers.Input(shape=(Ne,)),
          tf.keras.layers.Dense(Nneu, activation='tanh'),
          tf.keras.layers.Dense(Ns, activation='softmax'),
      ])
    
model.compile(
              #optimizer=tf.keras.optimizers.SGD(learning_rate=0.01,momentum=0.95),  
              optimizer=tf.keras.optimizers.Adam(lr=0.01),
              loss='categorical_crossentropy',
              #loss=keras.losses.MeanSquaredError(),
              metrics=['accuracy']
              )

# Muestra la configuración de la red
model.summary()    

In [ ]:
# Se entrena el modelo
model.fit(xTrainDS,eTrainDS,batch_size=250,epochs=Niter)

In [ ]:
oTrain=model.predict(xTrainDS)
oVal=model.predict(xValD)
oTest=model.predict(xTestD)
        
yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

PaTrain=100*accuracy_score(yTrainDS,yTrainE)
PaVal=100*accuracy_score(yVal,yValE)
PaTest=100*accuracy_score(yTest,yTestE)

print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<font size=4, color=blue>Red neuronal de 4 capas ocultas (con dropout)

In [ ]:
#import tensorflow as tf
tf.keras.backend.clear_session()

Nneu1=225
Nneu2=225
Nneu3=225
Nneu4=225

pDO=[0.1,0.3,0.3,0.3,0.3]

(Np,Ne)=np.shape(xTrainDS)

model = tf.keras.Sequential()
model.add(tf.keras.Input(shape=(Ne,)))
model.add(tf.keras.layers.Dropout(pDO[0]))
model.add(tf.keras.layers.Dense(Nneu1, activation='relu'))
model.add(tf.keras.layers.Dropout(pDO[1]))
model.add(tf.keras.layers.Dense(Nneu2, activation='relu'))
model.add(tf.keras.layers.Dropout(pDO[2]))
model.add(tf.keras.layers.Dense(Nneu3, activation='relu'))
model.add(tf.keras.layers.Dropout(pDO[3]))
model.add(tf.keras.layers.Dense(Nneu4, activation='relu'))
model.add(tf.keras.layers.Dropout(pDO[4]))
model.add(tf.keras.layers.Dense(10, activation='softmax'))

model.compile(optimizer=tf.keras.optimizers.Adam(lr=0.01),
              loss='categorical_crossentropy',
              metrics=['accuracy'])

# Muestra la configuración de la red
model.summary()

In [ ]:
# Se entrena el modelo
model.fit(xTrainDS,eTrainDS,batch_size=250,epochs=300)

In [ ]:
# Se evalúan las prestaciones
oTrain=model.predict(xTrainDS)
oVal=model.predict(xValD)
oTest=model.predict(xTestD)
        
yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

PaTrain=100*accuracy_score(yTrainDS,yTrainE)
PaVal=100*accuracy_score(yVal,yValE)
PaTest=100*accuracy_score(yTest,yTestE)

print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<font size=4, color=blue>Red neuronal de 4 capas ocultas (con dropout y batch-normalization)

In [ ]:
#import tensorflow as tf
tf.keras.backend.clear_session()

Nneu1=225
Nneu2=225
Nneu3=225
Nneu4=225

pDO=[0.1,0.3,0.3,0.3,0.3]

(Np,Ne)=np.shape(xTrainDS)

model = tf.keras.Sequential()
model.add(tf.keras.Input(shape=(Ne,)))
model.add(tf.keras.layers.Dropout(pDO[0]))
model.add(tf.keras.layers.Dense(Nneu1, activation='relu'))
model.add(tf.keras.layers.BatchNormalization())
model.add(tf.keras.layers.Dropout(pDO[1]))
model.add(tf.keras.layers.Dense(Nneu2, activation='relu'))
model.add(tf.keras.layers.BatchNormalization())
model.add(tf.keras.layers.Dropout(pDO[2]))
model.add(tf.keras.layers.Dense(Nneu3, activation='relu'))
model.add(tf.keras.layers.BatchNormalization())
model.add(tf.keras.layers.Dropout(pDO[3]))
model.add(tf.keras.layers.Dense(Nneu4, activation='relu'))
model.add(tf.keras.layers.BatchNormalization())
model.add(tf.keras.layers.Dropout(pDO[4]))
model.add(tf.keras.layers.Dense(10, activation='softmax'))

model.compile(optimizer=tf.keras.optimizers.Adam(lr=0.01),
              loss='categorical_crossentropy',
              metrics=['accuracy'])

# Muestra la configuración de la red
model.summary()

In [ ]:
# Se entrena el modelo
model.fit(xTrainDS,eTrainDS,batch_size=250,epochs=300)

In [ ]:
# Se evalúan las prestaciones
oTrain=model.predict(xTrainDS)
oVal=model.predict(xValD)
oTest=model.predict(xTestD)
        
yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

PaTrain=100*accuracy_score(yTrainDS,yTrainE)
PaVal=100*accuracy_score(yVal,yValE)
PaTest=100*accuracy_score(yTest,yTestE)

print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))

<br>
<font size=6, color=green>Red neuronal convolucional (CNN)
    
<font size=4, color=blue>Se entrenará ahora una red neuronal convolucional

<font size=4, color=blue>Parámetros generales de la red

In [ ]:
# Parámetros generales de la red en función de la resolución
Nepoch=10      # Número de épocas
Nbatch=250     # Número de muestras de cada mini-batch
pDO=0.3        # Probabilidad de dropout

if xTrainDS.shape[1]==100:
    Npix=10    # Número de píxeles por dirección        
    Nconv1=3   # Tamaño del filtro convolucional 1 (píxeles)
    Nconv2=3   # Tamaño del filtro convolucional 2 (píxeles) 
    Nfil1=16   # Número de filtros de la primera etapa
    Nfil2=32   # Número de filtros de la segunda etapa
    Nneu=512   # Número de neuronas del MLP final
elif xTrainDS.shape[1]==196:
    Npix=14    # Número de píxeles por dirección        
    Nconv1=3   # Tamaño del filtro convolucional 1 (píxeles)
    Nconv2=3   # Tamaño del filtro convolucional 2 (píxeles) 
    Nfil1=32   # Número de filtros de la primera etapa
    Nfil2=64   # Número de filtros de la segunda etapa
    Nneu=1024  # Número de neuronas del MLP final
elif xTrainDS.shape[1]==784:
    Npix=28    # Número de píxeles por dirección        
    Nconv1=5   # Tamaño del filtro convolucional 1 (píxeles)
    Nconv2=5   # Tamaño del filtro convolucional 2 (píxeles) 
    Nfil1=32   # Número de filtros de la primera etapa
    Nfil2=64   # Número de filtros de la segunda etapa
    Nneu=1024  # Número de neuronas del MLP final
              

<font size=4, color=blue>Definición de la estructura de la red CNN usando TensorFlow y Keras

In [ ]:
# Se define la estructura básica de la red CNN usando TensorFlow y Keras
#import tensorflow as tf
tf.keras.backend.clear_session()

model = tf.keras.Sequential(
  [
      tf.keras.layers.Reshape(input_shape=(Npix*Npix,), target_shape=(Npix, Npix, 1)),
      tf.keras.layers.Conv2D(kernel_size=Nconv1, filters=Nfil1, activation='relu', padding='same'),
      tf.keras.layers.MaxPooling2D((2, 2)),
      tf.keras.layers.Conv2D(kernel_size=Nconv2, filters=Nfil2, activation='relu', padding='same'),
      #tf.keras.layers.MaxPooling2D((2, 2)),
      tf.keras.layers.Flatten(),
      tf.keras.layers.Dense(Nneu, activation='relu'),
      #tf.keras.layers.Dropout(pDO),
      tf.keras.layers.Dense(10, activation='softmax')
  ])
    
    
model.compile(optimizer=tf.keras.optimizers.Adam(lr=0.01),
              loss='categorical_crossentropy',
              metrics=['accuracy'])
    
model.summary()

<font size=4, color=blue>Entrenamiento y evaluación de la red CNN

In [ ]:
model.fit(xTrainDS,eTrainDS,
          batch_size=Nbatch,
          epochs=Nepoch,
          validation_split = 0,
          #validation_data=(xValD, eVal),
          initial_epoch=0,
         )
    
oTrain=model.predict(xTrainDS)
oVal=model.predict(xValD)
oTest=model.predict(xTestD)
        
yTrainE=oTrain.argmax(axis=1)
yValE=oVal.argmax(axis=1)
yTestE=oTest.argmax(axis=1)

PaTrain=100*accuracy_score(yTrainDS,yTrainE)
PaVal=100*accuracy_score(yVal,yValE)
PaTest=100*accuracy_score(yTest,yTestE)
        
print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))
    

<font size=4, color=blue>Entrenamiento y evaluación de la red CNN sobre más iteraciones

In [ ]:
NiterPaso=2        # Número de iteraciones por paso 
NrepBucle=20       # Número de pasos de entrenamiento
evoPa=np.zeros((3,NrepBucle))

for kRep in range(NrepBucle):
    if kRep==0:
        model.fit(xTrainDS,eTrainDS,batch_size=Nbatch,epochs=NiterPaso,initial_epoch=0,verbose=0)
    else:
        model.fit(xTrainDS,eTrainDS,batch_size=Nbatch,epochs=NiterPaso,initial_epoch=1,verbose=0)
    
    oTrain=model.predict(xTrainDS)
    oVal=model.predict(xValD)
    oTest=model.predict(xTestD)
        
    yTrainE=oTrain.argmax(axis=1)
    yValE=oVal.argmax(axis=1)
    yTestE=oTest.argmax(axis=1)
    
    PaTrain=100*accuracy_score(yTrainDS,yTrainE)
    PaVal=100*accuracy_score(yVal,yValE)
    PaTest=100*accuracy_score(yTest,yTestE)
           
    print('Repetición %d de %d'%(kRep+1,NrepBucle))
    print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
    print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
    print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))
    print('--------------------------------------')
    
    evoPa[:,kRep]=[PaTrain,PaVal,PaTest]


font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
ejeIter=NiterPaso*np.linspace(1,NrepBucle,NrepBucle)
plt.plot(ejeIter,evoPa[0,:],ejeIter,evoPa[1,:],ejeIter,evoPa[2,:])
plt.title('Evolucion de la Prob. Acierto', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Prob Acierto (%)', fontdict=font)

print('Entrenamiento (azul) - Validación (Naranja) - Test (verde)')
print(' ')
print('Max. Pa (Entrenamiento): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[0,:]),NiterPaso*np.argmax(evoPa[0,:])))
print('Max. Pa (Validación): %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[1,:]),NiterPaso*np.argmax(evoPa[1,:])))
print('Max. Pa (Test) : %3.2f %% (Iter. %3.2f)'%(np.max(evoPa[2,:]),NiterPaso*np.argmax(evoPa[2,:])))
print('Resultado con validación (Test): %2.2f %%'%(evoPa[2,np.argmax(evoPa[1,:])]))   

<font size=4, color=blue>Se puede añadir dropout o batch normalization en la CNN

In [ ]:
# Se define la estructura básica de la red CNN usando TensorFlow y Keras
#import tensorflow as tf
tf.keras.backend.clear_session()

Nneu=1024

model = tf.keras.Sequential(
  [
      tf.keras.layers.Reshape(input_shape=(Npix*Npix,), target_shape=(Npix, Npix, 1)),
      tf.keras.layers.Conv2D(kernel_size=Nconv1, filters=Nfil1, activation='relu', padding='same'),
      tf.keras.layers.MaxPooling2D((2, 2)),
      tf.keras.layers.Conv2D(kernel_size=Nconv2, filters=Nfil2, activation='relu', padding='same'),
      #tf.keras.layers.MaxPooling2D((2, 2)),
      tf.keras.layers.Flatten(),
      tf.keras.layers.Dense(Nneu, activation='relu'),
      tf.keras.layers.BatchNormalization(),
      tf.keras.layers.Dropout(0.3),
      tf.keras.layers.Dense(10, activation='softmax')
  ])
    
    
model.compile(optimizer=tf.keras.optimizers.Adam(lr=0.01),
              loss='categorical_crossentropy',
              metrics=['accuracy'])
    
model.summary()

In [ ]:
NiterPaso=2        # Número de iteraciones por paso 
NrepBucle=50       # Número de pasos de entrenamiento
evoPa=np.zeros((3,NrepBucle))

for kRep in range(NrepBucle):
    if kRep==0:
        model.fit(xTrainDS,eTrainDS,batch_size=Nbatch,epochs=NiterPaso,initial_epoch=0,verbose=0)
    else:
        model.fit(xTrainDS,eTrainDS,batch_size=Nbatch,epochs=NiterPaso,initial_epoch=1,verbose=0)
    
    oTrain=model.predict(xTrainDS)
    oVal=model.predict(xValD)
    oTest=model.predict(xTestD)
        
    yTrainE=oTrain.argmax(axis=1)
    yValE=oVal.argmax(axis=1)
    yTestE=oTest.argmax(axis=1)
    
    PaTrain=100*accuracy_score(yTrainDS,yTrainE)
    PaVal=100*accuracy_score(yVal,yValE)
    PaTest=100*accuracy_score(yTest,yTestE)
                 
    print('Repetición %d de %d'%(kRep+1,NrepBucle))
    print('Probabilidad de acierto (Train): %2.2f %%'%(PaTrain))
    print('Probabilidad de acierto (Valida): %2.2f %%'%(PaVal))
    print('Probabilidad de acierto (Test): %2.2f %%'%(PaTest))
    print('--------------------------------------')
    
    evoPa[:,kRep]=[PaTrain,PaVal,PaTest]


font = {'family': 'serif','color':  'darkred','weight': 'normal','size': 16}
ejeIter=NiterPaso*np.linspace(1,NrepBucle,NrepBucle)
plt.plot(ejeIter,evoPa[0,:],ejeIter,evoPa[1,:],ejeIter,evoPa[2,:])
plt.title('Evolucion de la Prob. Acierto', fontdict=font)
plt.xlabel('Iteración', fontdict=font)
plt.ylabel('Prob Acierto (%)', fontdict=font)

print('Entrenamiento (azul) - Validación (Naranja) - Test (verde)')
print(' ')
print('Max. Pa (Entrenamiento): %3.2f (Iter. %3.2f)'%(np.max(evoPa[0,:]),NiterPaso*np.argmax(evoPa[0,:])))
print('Max. Pa (Validación): %3.2f (Iter. %3.2f)'%(np.max(evoPa[1,:]),NiterPaso*np.argmax(evoPa[1,:])))
print('Max. Pa (Test) : %3.2f (Iter. %3.2f)'%(np.max(evoPa[2,:]),NiterPaso*np.argmax(evoPa[2,:])))
print('Resultado con validación (Test): %s'%(evoPa[2,np.argmax(evoPa[1,:])]))   

In [ ]:
import importlib
importlib.reload(mdl)
#mdl=reload(mdl)